#  Consignes

## Description

Ouvrir le fichier ks-projects-201801.csv, il recense environ 100 000 projets KickStarter. Intégrer les données directement avec L'API Python dans une base de données Mongo. 

Il conviendra de bien spécifier manuellement l'ID du document. Pensez aussi à bien formatter le type des données pour profiter des méthodes implémentées par Mongo. L'ensemble de données n'est pas forcément nécessaire, c'est à vous de créer votre modèle de données.

## Questions

- 1) Récupérer les 5 projets ayant reçu le plus de promesse de dons.
- 2) Compter le nombre de projets ayant atteint leur but.
- 3) Compter le nombre de projets pour chaque catégorie.
- 4) Compter le nombre de projets français ayant été instanciés avant 2016.
- 5) Récupérer les projets américains ayant demandé plus de 200 000 dollars.
- 6) Compter le nombre de projet ayant "Sport" dans leur nom

In [1]:
import pandas as pd
import pymongo

In [45]:
client = pymongo.MongoClient()
database = client['exercices']
collection = database['kickstarter']

In [47]:
df_ks = pd.read_csv("./data/ks-projects-201801-sample.csv")
df_ks.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 150000 entries, 0 to 149999
Data columns (total 14 columns):
 #   Column            Non-Null Count   Dtype  
---  ------            --------------   -----  
 0   ID                150000 non-null  int64  
 1   name              149998 non-null  object 
 2   category          150000 non-null  object 
 3   main_category     150000 non-null  object 
 4   currency          150000 non-null  object 
 5   deadline          150000 non-null  object 
 6   goal              150000 non-null  object 
 7   launched          150000 non-null  object 
 8   pledged           150000 non-null  object 
 9   state             150000 non-null  object 
 10  backers           150000 non-null  object 
 11  country           150000 non-null  object 
 12  usd pledged       148518 non-null  object 
 13  usd_pledged_real  150000 non-null  float64
dtypes: float64(1), int64(1), object(12)
memory usage: 16.0+ MB


C:\Users\march\AppData\Local\Temp\ipykernel_20832\1859761035.py:1: DtypeWarning: Columns (6,8,10,12) have mixed types. Specify dtype option on import or set low_memory=False.
  df_ks = pd.read_csv("./data/ks-projects-201801-sample.csv")


Ce warning intervient lorsque pandas n'arrive pas à inférer le type de données. Il est sympa il précise les colones 6,8,10,12. 

In [48]:
df_ks.columns[[6,8,10,12]]

Index(['goal', 'pledged', 'backers', 'usd pledged'], dtype='object')

## Question 0

### Nettoyer les données

In [49]:
# df_ks.info()

In [50]:

df_ks= df_ks.dropna()
df_ks= df_ks[df_ks["ID"]!=85964225]
df_ks["deadline"]=pd.to_datetime(df_ks["deadline"])
df_ks['launched']=pd.to_datetime(df_ks["launched"])
new_type = {'ID':int,'name':str,'category':str,'main_category':str,'currency':str,'state':str,'goal': float, 'pledged': float, 'backers': int, 'usd pledged': float,'country':str,'usd_pledged_real':float}

df_ks=df_ks.astype(new_type)

df_ks.info()


<class 'pandas.core.frame.DataFrame'>
Index: 148515 entries, 0 to 149999
Data columns (total 14 columns):
 #   Column            Non-Null Count   Dtype         
---  ------            --------------   -----         
 0   ID                148515 non-null  int32         
 1   name              148515 non-null  object        
 2   category          148515 non-null  object        
 3   main_category     148515 non-null  object        
 4   currency          148515 non-null  object        
 5   deadline          148515 non-null  datetime64[ns]
 6   goal              148515 non-null  float64       
 7   launched          148515 non-null  datetime64[ns]
 8   pledged           148515 non-null  float64       
 9   state             148515 non-null  object        
 10  backers           148515 non-null  int32         
 11  country           148515 non-null  object        
 12  usd pledged       148515 non-null  float64       
 13  usd_pledged_real  148515 non-null  float64       
dtypes: dateti

### Importer les données

In [51]:
data = df_ks.to_dict(orient="records")
collection.insert_many(data)

InsertManyResult([ObjectId('656f96879db24575c148e6f4'), ObjectId('656f96879db24575c148e6f5'), ObjectId('656f96879db24575c148e6f6'), ObjectId('656f96879db24575c148e6f7'), ObjectId('656f96879db24575c148e6f8'), ObjectId('656f96879db24575c148e6f9'), ObjectId('656f96879db24575c148e6fa'), ObjectId('656f96879db24575c148e6fb'), ObjectId('656f96879db24575c148e6fc'), ObjectId('656f96879db24575c148e6fd'), ObjectId('656f96879db24575c148e6fe'), ObjectId('656f96879db24575c148e6ff'), ObjectId('656f96879db24575c148e700'), ObjectId('656f96879db24575c148e701'), ObjectId('656f96879db24575c148e702'), ObjectId('656f96879db24575c148e703'), ObjectId('656f96879db24575c148e704'), ObjectId('656f96879db24575c148e705'), ObjectId('656f96879db24575c148e706'), ObjectId('656f96879db24575c148e707'), ObjectId('656f96879db24575c148e708'), ObjectId('656f96879db24575c148e709'), ObjectId('656f96879db24575c148e70a'), ObjectId('656f96879db24575c148e70b'), ObjectId('656f96879db24575c148e70c'), ObjectId('656f96879db24575c148e7

## Question 1
Récupérer les 5 projets ayant reçu le plus de promesse de dons.

In [54]:
cur = collection.find().sort([("usd pledged",-1)])
for i in range(5):
    project = cur.next()
    print(project["name"])

COOLEST COOLER: 21st Century Cooler that's Actually Cooler
Pebble 2, Time 2 + All-New Pebble Core
OUYA: A New Kind of Video Game Console
Pono Music - Where Your Soul Rediscovers Music
The Veronica Mars Movie Project


## Question 2
Compter le nombre de projets ayant atteint leur but.

In [56]:
collection.count_documents({"state":"successful"})

52998

## Question 3
Compter le nombre de projets pour chaque catégorie.

In [62]:
result = collection.aggregate([{"$group": {"_id":"$category","count":{"$sum":1}}}])
for res in result:
    print(f"Category : {res['_id']}, nombre de projet : {res['count']}")

Category : Jazz, nombre de projet : 733
Category : Product Design, nombre de projet : 8885
Category : Makerspaces, nombre de projet : 91
Category : Immersive, nombre de projet : 131
Category : Glass, nombre de projet : 51
Category : Ready-to-wear, nombre de projet : 332
Category : Tabletop Games, nombre de projet : 5579
Category : Theater, nombre de projet : 2786
Category : Music Videos, nombre de projet : 299
Category : Video Games, nombre de projet : 4797
Category : Couture, nombre de projet : 108
Category : Art, nombre de projet : 3358
Category : Games, nombre de projet : 1331
Category : Musical, nombre de projet : 367
Category : Childrenswear, nombre de projet : 192
Category : Audio, nombre de projet : 164
Category : Rock, nombre de projet : 2707
Category : Woodworking, nombre de projet : 433
Category : Food, nombre de projet : 4612
Category : Painting, nombre de projet : 1288
Category : Installations, nombre de projet : 178
Category : Weaving, nombre de projet : 38
Category : Illu

## Question 4
Compter le nombre de projets français ayant été instanciés avant 2016.

In [65]:
from datetime import datetime
date = datetime.strptime("2016-01-01", "%Y-%m-%d")
collection.count_documents({"$and" : [{"country":"FR"},{"launched":{"$lt" : date}}]})

330

## Question 5
Récupérer les projets américains ayant demandé plus de 200 000 dollars.

In [67]:
res = collection.find({"$and" : [{"country":"US"},{"usd pledged":{"$gte" : 200000}}]})
for i in res:
    print(i["name"])


The uKeg Pressurized Growler for Fresh Beer
Redux COURG - Hybrid Watches with Missions to Tackle
Legion Solar - A Better Way to Energy Independence
Edyn: Welcome to the connected garden.
Period Panties
Shadowrun: Hong Kong
Kurt Vonnegut: Unstuck in Time
Battle Worlds: Kronos - Turn-based strategy revisited
Hie Diaper Bag: Your New Best Friend
Hemingwrite - A Distraction Free Digital Typewriter
Dobot: Robotic Arm for Everyone, Arduino & Open Source
PolySmooth & Polysher: 3D Prints Without Layers
Sails of Glory - Miniatures Ship Combat
The Temperfect Mug: Coffee and Tea at The Perfect Temp
Planetary Annihilation - A Next Generation RTS
Aeon's End: War Eternal
XERISCOPE: The Orbiting Mechanical Automatic Watch by XERIC
Canary in a Coal Mine
Akaneiro: Demon Hunters
MYTH: Journeyman
The ultimate sleep sanctuary: Kokoon EEG headphones
Iota: Never lose sight of what's important.
Pixy (CMUcam5): a fast, easy-to-use vision sensor
Reissue of the 1975 NASA Graphics Standards Manual.
Unsung Story:

## Question 6
Compter le nombre de projet ayant "Sport" dans leur nom

In [72]:
collection.count_documents({"name":{"$regex" :"Sport", "$options":"i"}})

500